In [1]:
import numpy as np
import itertools
import time
from collections import Counter

In [2]:
scene = {
    (0,0): 'red,metal,sphere',
    (0,1):'green,matte,cube',
    (1,1):'blue,metal,cube'
}

In [3]:
def make_base_paths(scene):
    '''make base point A to B position paths from scene'''
    paths = set()
    for pos1, pos2 in itertools.product(*[scene.keys(), scene.keys()]):
        i1, j1 = pos1
        i2, j2 = pos2
        horizontal = i1 == i2
        vertical = j1 == j2
        
        path = None
        if horizontal and abs(j1-j2)==1:
            if j1 > j2:
                path = (pos1, 'RL', pos2)
            else:
                path = (pos1, 'LR', pos2)
        if vertical and abs(i1-i2)==1:
            if i1 > i2:
                path = (pos1, 'BA', pos2)
            else:
                path = (pos1, 'AB', pos2)
        if path: paths.add(path)
    return paths

In [4]:
def connect_paths(paths):
    '''connect base paths into longer paths'''
    new_paths = set()
    for path1, path2 in itertools.combinations(paths, 2):
        s1, e1 = path1[0], path1[-1]
        s2, e2 = path2[0], path2[-1]
        new_path = None
        
        # TODO check that path doesn't overlap itself?
        if (e1 == s2 and not(set(path1[::2][:-1]) & set(path2[::2][1:]))):
            new_path = (s1,) + path1[1:-1] + (e1,) + path2[1:-1] + (e2,)
        elif (s1 == e2 and not(set(path1[::2][1:]) & set(path2[::2][:-1]))):
            new_path = (s2,) + path2[1:-1] + (e2,) + path1[1:-1] + (e1,)
        if new_path: new_paths.add(new_path)
    return new_paths

connect_paths(make_base_paths(scene))

{((0, 0), 'LR', (0, 1), 'AB', (1, 1)), ((1, 1), 'BA', (0, 1), 'RL', (0, 0))}

In [5]:
def translate_paths(paths, scene):
    '''translate position paths into obj attr paths'''
    translated_paths = set()
    for p in paths:
#         translated_path = tuple('\('+scene[x]+'\)' if isinstance(x, tuple) else x for x in p)
#         translated_path = '-'.join(translated_path)
        translated_path = tuple(scene[x] if isinstance(x, tuple) else x for x in p)
        translated_paths.add(translated_path)
    return translated_paths
    
translate_paths(connect_paths(make_base_paths(scene)), scene)

{('blue,metal,cube', 'BA', 'green,matte,cube', 'RL', 'red,metal,sphere'),
 ('red,metal,sphere', 'LR', 'green,matte,cube', 'AB', 'blue,metal,cube')}

In [6]:
def swap_object_attr(p, attributes, num_swaps, debug=False):
    '''swap out num_swaps object attributes to make a negative example'''
    
    p = list(p)
    if debug: print(p)
        
    swap_pos_all = np.random.choice(list(range(len(p))[::2]), size=min(int(num_swaps), len(p)//2), replace=False)
    attr_pos_all = np.random.choice(3, size=int(num_swaps))

    for swap_pos, attr_pos in zip(swap_pos_all, attr_pos_all):
        if debug:
            print(swap_pos, p[swap_pos], attr_pos, p[swap_pos].split(',')[attr_pos])
        
        if attr_pos == 0:
            attr_options = attributes['colors']
        elif attr_pos == 1:
            attr_options = attributes['textures']
        else:
            attr_options = attributes['shapes']
        
        obj_attrs = p[swap_pos].split(',')
        old_attr = obj_attrs[attr_pos]
        new_attr = old_attr
        while new_attr == old_attr:
            print('while loop within swap_object_attr')
            new_attr = np.random.choice(attr_options)
        obj_attrs[attr_pos] = new_attr
        p[swap_pos] = ','.join(obj_attrs)

    if debug: print(p)
    return tuple(p)

In [7]:
def swap_relations(p, attributes, num_swaps, debug=False):
    '''swap out num_swaps object relations to make a negative example'''
    
    p = list(p)
    if debug: print(p)
    swap_pos_all = np.random.choice(list(range(len(p))[1::2]), size=min(int(num_swaps), len(p)//2), replace=False)
    attr_options = attributes['relations']
    for swap_pos in swap_pos_all:
        if debug:
            print(swap_pos, p[swap_pos])
        old_attr = p[swap_pos]
        new_attr = old_attr
        while new_attr == old_attr:
            print('while loop within swap_relations')
            new_attr = np.random.choice(attr_options)
        p[swap_pos] = new_attr
        
    if debug: print(p)
    return tuple(p)

In [8]:
def make_all_paths(scene, attributes, num_levels=3, num_swaps=1):
    
    # 3 levels of paths
    base_paths = make_base_paths(scene) # single straight edge
    gt_position_paths = base_paths
    for i in range(num_levels):
        gt_position_paths = gt_position_paths | connect_paths(gt_position_paths)
    
    # positive paths  
    positive_objattr_paths = translate_paths(gt_position_paths, scene)
    
    # sample negative paths by swapping
    negative_objattr_attr_paths = set()
    for pos_p_i, pos_p in enumerate(positive_objattr_paths):
        # either swap a relation or an attribute
        choice = np.random.choice(2)
        swap_fn = swap_relations if choice == 0 else swap_object_attr
        neg_p = pos_p
        retry = 0
        while neg_p in positive_objattr_paths:
            print(f'{pos_p_i} while loop within make_all_paths, rety={retry}')
            retry += 1
            if retry == 5:
                break 
            neg_p = swap_fn(pos_p, attributes, num_swaps)
            
        if neg_p not in positive_objattr_paths:
            negative_objattr_attr_paths.add(neg_p)
    
    assert not (positive_objattr_paths & negative_objattr_attr_paths)
    return gt_position_paths, positive_objattr_paths, negative_objattr_attr_paths

In [9]:
def sample_scene(num_slots, grid_dim, attributes):
    assert num_slots <= grid_dim**2
    all_positions = list((i,j) for i,j in itertools.product(range(grid_dim), range(grid_dim)))
    indices = np.random.choice(len(all_positions), num_slots, replace=False)
    scene_positions = list(all_positions[idx] for idx in indices)
    scene_shapes = np.random.choice(attributes['shapes'], size=num_slots)
    scene_colors = np.random.choice(attributes['colors'], size=num_slots)
    scene_materials = np.random.choice(attributes['textures'], size=num_slots)
    scene = {
        pos: ','.join([c,m,s]) for pos, c, m, s in \
        zip(scene_positions, scene_colors, scene_materials, scene_shapes)
    }
    metadata = {'grid_dim':grid_dim, 'num_slots':num_slots}
    return scene, metadata

In [50]:
def make_scene_input(scene, metadata):
    scene_input = []
    for i in range(metadata['grid_dim']):
        for j in range(metadata['grid_dim']):
            if (i,j) in scene:
                c, t, s = scene[(i,j)].split(',')
                scene_input.append((i, j, c, t, s))
            else:
                scene_input.append((i, j, 'none', 'none', 'none'))
    return scene_input

                
# ToDo input query format
def make_query_input(objattr_path):
#     return '-'.join(f'({s})' if i%2==0 else s for i,s in enumerate(objattr_path))/
    return ' - '.join(f'( {s.replace(",", " ")} )' if i%2==0 else s for i,s in enumerate(objattr_path))

In [11]:
def abbreviate(obj_attr_str):
    '''red,metal,cube to rmc'''
    return ''.join([s[0] for s in obj_attr_str.split(',')])

def plot_scene(scene, metadata):
    for i in range(metadata['grid_dim']):
        print(' - '.join([abbreviate(scene.get((i,j), ' , , ')) for j in range(metadata['grid_dim'])]))
        print('   '.join([f'{i},{j}' for j in range(metadata['grid_dim'])]))
        if not i == metadata['grid_dim']-1:
            print('   '.join([f' | ' for j in range(metadata['grid_dim'])]))

## Sample One Scene

In [52]:
attributes = {
    'colors': ['red', 'green', 'blue'],
    'textures': ['metal', 'rubber'],
    'shapes': ['cube', 'sphere', 'tetrahedron'],
    'relations': ['RL', 'LR', 'AB', 'BA']
}

np.random.seed(39)

scene, metadata = sample_scene(num_slots=18, grid_dim=6, attributes=attributes)

plot_scene(scene, metadata)

gt_position_paths, positive_objattr_paths, negative_objattr_paths = make_all_paths(scene, attributes, num_levels=4, num_swaps=1)

    - grc - bms -     -     - grs
0,0   0,1   0,2   0,3   0,4   0,5
 |     |     |     |     |     | 
    - bmc - gmc -     - gms -    
1,0   1,1   1,2   1,3   1,4   1,5
 |     |     |     |     |     | 
    -     -     - brc -     -    
2,0   2,1   2,2   2,3   2,4   2,5
 |     |     |     |     |     | 
rmc - gms -     - gmt - gmc -    
3,0   3,1   3,2   3,3   3,4   3,5
 |     |     |     |     |     | 
gms -     - rrt -     - brc - grt
4,0   4,1   4,2   4,3   4,4   4,5
 |     |     |     |     |     | 
    - bms - rmc -     -     - rmc
5,0   5,1   5,2   5,3   5,4   5,5
0 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
1 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
2 while loop within make_all_paths, rety=0
while loop within swap_object_attr
3 while loop within make_all_paths, rety=0
while loop within swap_relations
while loop within swap_relations
4 while l

In [53]:
print(make_scene_input(scene, metadata))
print('----------------------------------------')
print(make_query_input(('blue,metal,sphere', 'AB', 'green,metal,cube')))

[(0, 0, 'none', 'none', 'none'), (0, 1, 'green', 'rubber', 'cube'), (0, 2, 'blue', 'metal', 'sphere'), (0, 3, 'none', 'none', 'none'), (0, 4, 'none', 'none', 'none'), (0, 5, 'green', 'rubber', 'sphere'), (1, 0, 'none', 'none', 'none'), (1, 1, 'blue', 'metal', 'cube'), (1, 2, 'green', 'metal', 'cube'), (1, 3, 'none', 'none', 'none'), (1, 4, 'green', 'metal', 'sphere'), (1, 5, 'none', 'none', 'none'), (2, 0, 'none', 'none', 'none'), (2, 1, 'none', 'none', 'none'), (2, 2, 'none', 'none', 'none'), (2, 3, 'blue', 'rubber', 'cube'), (2, 4, 'none', 'none', 'none'), (2, 5, 'none', 'none', 'none'), (3, 0, 'red', 'metal', 'cube'), (3, 1, 'green', 'metal', 'sphere'), (3, 2, 'none', 'none', 'none'), (3, 3, 'green', 'metal', 'tetrahedron'), (3, 4, 'green', 'metal', 'cube'), (3, 5, 'none', 'none', 'none'), (4, 0, 'green', 'metal', 'sphere'), (4, 1, 'none', 'none', 'none'), (4, 2, 'red', 'rubber', 'tetrahedron'), (4, 3, 'none', 'none', 'none'), (4, 4, 'blue', 'rubber', 'cube'), (4, 5, 'green', 'rubbe

In [14]:
positive_objattr_paths

{('blue,metal,cube', 'BA', 'green,rubber,cube'),
 ('blue,metal,cube', 'BA', 'green,rubber,cube', 'LR', 'blue,metal,sphere'),
 ('blue,metal,cube',
  'BA',
  'green,rubber,cube',
  'LR',
  'blue,metal,sphere',
  'AB',
  'green,metal,cube'),
 ('blue,metal,cube', 'LR', 'green,metal,cube'),
 ('blue,metal,cube', 'LR', 'green,metal,cube', 'BA', 'blue,metal,sphere'),
 ('blue,metal,cube',
  'LR',
  'green,metal,cube',
  'BA',
  'blue,metal,sphere',
  'RL',
  'green,rubber,cube'),
 ('blue,metal,sphere', 'AB', 'green,metal,cube'),
 ('blue,metal,sphere', 'AB', 'green,metal,cube', 'RL', 'blue,metal,cube'),
 ('blue,metal,sphere',
  'AB',
  'green,metal,cube',
  'RL',
  'blue,metal,cube',
  'BA',
  'green,rubber,cube'),
 ('blue,metal,sphere', 'LR', 'red,metal,cube'),
 ('blue,metal,sphere', 'LR', 'red,metal,cube', 'BA', 'red,rubber,tetrahedron'),
 ('blue,metal,sphere', 'RL', 'green,rubber,cube'),
 ('blue,metal,sphere', 'RL', 'green,rubber,cube', 'AB', 'blue,metal,cube'),
 ('blue,metal,sphere',
  'RL',

In [16]:
len(positive_objattr_paths)

66

In [19]:
negative_objattr_paths

{('blue,metal,cube', 'AB', 'green,metal,cube', 'BA', 'blue,metal,sphere'),
 ('blue,metal,cube', 'LR', 'blue,metal,cube'),
 ('blue,metal,cube',
  'LR',
  'blue,metal,cube',
  'BA',
  'blue,metal,sphere',
  'RL',
  'green,rubber,cube'),
 ('blue,metal,cube',
  'LR',
  'green,rubber,cube',
  'LR',
  'blue,metal,sphere',
  'AB',
  'green,metal,cube'),
 ('blue,metal,cube', 'RL', 'green,rubber,cube'),
 ('blue,metal,cube', 'RL', 'green,rubber,cube', 'LR', 'blue,metal,sphere'),
 ('blue,metal,sphere', 'AB', 'green,metal,cube', 'BA', 'blue,metal,cube'),
 ('blue,metal,sphere',
  'AB',
  'green,metal,cube',
  'RL',
  'blue,metal,cube',
  'BA',
  'green,metal,cube'),
 ('blue,metal,sphere', 'BA', 'green,rubber,cube', 'AB', 'blue,metal,cube'),
 ('blue,metal,sphere', 'RL', 'blue,rubber,cube'),
 ('blue,metal,sphere', 'RL', 'green,metal,cube'),
 ('blue,metal,sphere',
  'RL',
  'green,rubber,cube',
  'AB',
  'red,metal,cube',
  'LR',
  'green,metal,cube'),
 ('blue,metal,sphere', 'RL', 'red,metal,cube'),
 

In [20]:
len(negative_objattr_paths)

66

## Sample Many Scenes

In [27]:
np.random.seed(42)

num_scenes = 5000 # number of scenes
grid_dim = 3 # grid dimension
num_slots = 4 # number of slots to fill
num_levels = 3 # max path length = 2*4=16
num_swaps = 1  # number of attributes or relations to switch out for negative examples

attributes = {
    'colors': ['red', 'green', 'blue'],
    'textures': ['metal', 'rubber'],
    'shapes': ['cube', 'sphere', 'tetrahedron'],
    'relations': ['RL', 'LR', 'AB', 'BA']
}

start = time.time()
dataset = {}
for i in range(num_scenes):
    scene, metadata = sample_scene(num_slots, grid_dim, attributes)
    gt_position_paths, positive_objattr_paths, negative_objattr_paths = make_all_paths(scene, attributes, num_levels, num_swaps)
    p_lens = []
    for p in gt_position_paths:
        p_lens.append(len(p)//2)
    
    dataset[i] = {
        'scene': scene,
        'metadata': metadata,
        'gt_position_paths': gt_position_paths,
        'positive_objattr_paths': positive_objattr_paths,
        'negative_objattr_paths': negative_objattr_paths,
        'num_paths': len(gt_position_paths),
        'path_len_ctr': Counter(p_lens)
    }
print(time.time() - start, ' seconds')

0 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
1 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
0 while loop within make_all_paths, rety=0
while loop within swap_object_attr
1 while loop within make_all_paths, rety=0
while loop within swap_object_attr
2 while loop within make_all_paths, rety=0
while loop within swap_relations
while loop within swap_relations
3 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
4 while loop within make_all_paths, rety=0
while loop within swap_relations
5 while loop within make_all_paths, rety=0
while loop within swap_object_attr
6 while loop within make_all_paths, rety=0
while loop within swap_object_attr
7 while loop within make

while loop within swap_object_attr
16 while loop within make_all_paths, rety=0
while loop within swap_object_attr
17 while loop within make_all_paths, rety=0
while loop within swap_relations
18 while loop within make_all_paths, rety=0
while loop within swap_relations
while loop within swap_relations
19 while loop within make_all_paths, rety=0
while loop within swap_relations
20 while loop within make_all_paths, rety=0
while loop within swap_relations
while loop within swap_relations
while loop within swap_relations
while loop within swap_relations
21 while loop within make_all_paths, rety=0
while loop within swap_relations
22 while loop within make_all_paths, rety=0
while loop within swap_relations
23 while loop within make_all_paths, rety=0
while loop within swap_object_attr
0 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
1 while loop within make_all_paths, rety=0
while loop within swap_relations
2 while loop within make

while loop within swap_object_attr
while loop within swap_object_attr
3 while loop within make_all_paths, rety=0
while loop within swap_relations
while loop within swap_relations
4 while loop within make_all_paths, rety=0
while loop within swap_relations
5 while loop within make_all_paths, rety=0
while loop within swap_relations
while loop within swap_relations
0 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
1 while loop within make_all_paths, rety=0
while loop within swap_object_attr
2 while loop within make_all_paths, rety=0
while loop within swap_relations
while loop within swap_relations
3 while loop within make_all_paths, rety=0
while loop within swap_object_attr
4 while loop within make_all_paths, rety=0
while loop within swap_relations
5 while loop within make_all_paths, rety=0
while loop within swap_relations
0 while loop within make_all_paths, rety=0
while loop within swap_object_attr
1 while loop within make_all

8 while loop within make_all_paths, rety=0
while loop within swap_object_attr
9 while loop within make_all_paths, rety=0
while loop within swap_object_attr
10 while loop within make_all_paths, rety=0
while loop within swap_relations
while loop within swap_relations
while loop within swap_relations
11 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
12 while loop within make_all_paths, rety=0
while loop within swap_object_attr
13 while loop within make_all_paths, rety=0
while loop within swap_object_attr
14 while loop within make_all_paths, rety=0
while loop within swap_relations
14 while loop within make_all_paths, rety=1
while loop within swap_relations
15 while loop within make_all_paths, rety=0
while loop within swap_object_attr
16 while loop within make_all_paths, rety=0
while loop within swap_object_attr
17 while loop within make_all_paths, rety=0
while loop within swap_object_attr
18 while loop within make_all_paths, r

while loop within swap_object_attr
8 while loop within make_all_paths, rety=0
while loop within swap_object_attr
9 while loop within make_all_paths, rety=0
while loop within swap_object_attr
10 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
11 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
0 while loop within make_all_paths, rety=0
while loop within swap_relations
1 while loop within make_all_paths, rety=0
while loop within swap_relations
while loop within swap_relations
2 while loop within make_all_paths, rety=0
while loop within swap_relations
3 while loop within make_all_paths, rety=0
while loop within swap_relations

...

3 while loop within make_all_paths, rety=0
while loop within swap_relations
while loop within swap_relations
4 while loop within make_all_paths, rety=0
while loop within swap_relations
5 while loop within make_all_paths, rety=0
while loop within swap_relations
6 while loop within make_all_paths, rety=0
while loop within swap_object_attr
7 while loop within make_all_paths, rety=0
while loop within swap_relations
while loop within swap_relations
8 while loop within make_all_paths, rety=0
while loop within swap_object_attr
9 while loop within make_all_paths, rety=0
while loop within swap_relations
10 while loop within make_all_paths, rety=0
while loop within swap_object_attr
11 while loop within make_all_paths, rety=0
while loop within swap_object_attr
0 while loop within make_all_paths, rety=0
while loop within swap_relations
1 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
0 while loop wit

0 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
1 while loop within make_all_paths, rety=0
while loop within swap_object_attr
2 while loop within make_all_paths, rety=0
while loop within swap_relations
3 while loop within make_all_paths, rety=0
while loop within swap_relations
4 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
5 while loop within make_all_paths, rety=0
while loop within swap_object_attr
6 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
7 while loop within make_all_paths, rety=0
while loop within swap_relations
8 while loop within make_all_paths, rety=0
while loop within swap_o

while loop within swap_object_attr
while loop within swap_object_attr
1 while loop within make_all_paths, rety=0
while loop within swap_relations
2 while loop within make_all_paths, rety=0
while loop within swap_relations
3 while loop within make_all_paths, rety=0
while loop within swap_object_attr
4 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
5 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
while loop within swap_object_attr
0 while loop within make_all_paths, rety=0
while loop within swap_relations
1 while loop within make_all_paths, rety=0
while loop within swap_relations
2 while loop within make_all_paths, rety=0
while loop within swap_relations
3 while loop within make_all_paths, rety=0
while loop within swap_relations
4 while loop within make_all_paths, rety=0
while loop within swap_object_attr
5 while loop within ma

0 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
1 while loop within make_all_paths, rety=0
while loop within swap_object_attr
2 while loop within make_all_paths, rety=0
while loop within swap_relations
3 while loop within make_all_paths, rety=0
while loop within swap_relations
0 while loop within make_all_paths, rety=0
while loop within swap_object_attr
1 while loop within make_all_paths, rety=0
while loop within swap_relations
0 while loop within make_all_paths, rety=0
while loop within swap_relations
1 while loop within make_all_paths, rety=0
while loop within swap_relations
2 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
3 while loop within make_all_paths, rety=0
while loop within swap_relations
4 while loop within make_all_paths, rety=0
while loop within swap_object_attr
5 while loop within make_all_paths, rety=0
while loop within swap_relations
6 while 

while loop within swap_object_attr
while loop within swap_object_attr
9 while loop within make_all_paths, rety=0
while loop within swap_relations
10 while loop within make_all_paths, rety=0
while loop within swap_relations
11 while loop within make_all_paths, rety=0
while loop within swap_object_attr
0 while loop within make_all_paths, rety=0
while loop within swap_object_attr
while loop within swap_object_attr
1 while loop within make_all_paths, rety=0
while loop within swap_object_attr
2 while loop within make_all_paths, rety=0
while loop within swap_object_attr
3 while loop within make_all_paths, rety=0
while loop within swap_object_attr
4 while loop within make_all_paths, rety=0
while loop within swap_object_attr
5 while loop within make_all_paths, rety=0
while loop within swap_object_attr
0 while loop within make_all_paths, rety=0
while loop within swap_relations
1 while loop within make_all_paths, rety=0
while loop within swap_object_attr
2 while loop within make_all_paths, rety=

In [59]:
# 9 choose 4, 18 possibile attr combos each
126 * (18) * (18) * (18) * (18)

13226976

In [36]:
has_path_ct = 0
tot_path_len_ctr = Counter()
all_num_paths = []
all_gt_position_paths = []
all_positive_objattr_paths = []
all_negative_objattr_paths = []
for i in range(num_scenes):
    if dataset[i]['gt_position_paths']:
        has_path_ct += 1
        tot_path_len_ctr += dataset[i]['path_len_ctr']
        all_num_paths.append(dataset[i]['num_paths'])
        all_gt_position_paths += list(dataset[i]['gt_position_paths'])
        all_positive_objattr_paths += list(dataset[i]['positive_objattr_paths'])
        all_negative_objattr_paths += list(dataset[i]['negative_objattr_paths'])

In [56]:
sorted(dataset[0]['scene'].items())

[((0, 0), 'red,rubber,tetrahedron'),
 ((0, 1), 'blue,rubber,tetrahedron'),
 ((1, 2), 'green,rubber,tetrahedron'),
 ((2, 1), 'red,rubber,tetrahedron')]

In [37]:
# How many paths does each scene has?
Counter(all_num_paths).most_common()
# 1759 scenes have 6 paths

[(6, 1759), (12, 1268), (2, 1118), (4, 457), (24, 154)]

In [29]:
# overall path length counter
tot_path_len_ctr
# In total, there are 19940 1-step paths

Counter({1: 19940, 3: 3122, 2: 10468})

In [30]:
Counter(all_gt_position_paths).most_common()

[(((1, 1), 'LR', (1, 2)), 873),
 (((1, 2), 'RL', (1, 1)), 873),
 (((2, 1), 'BA', (1, 1)), 868),
 (((1, 1), 'AB', (2, 1)), 868),
 (((1, 2), 'AB', (2, 2)), 853),
 (((2, 2), 'BA', (1, 2)), 853),
 (((1, 0), 'AB', (2, 0)), 846),
 (((2, 0), 'BA', (1, 0)), 846),
 (((2, 2), 'RL', (2, 1)), 844),
 (((2, 1), 'LR', (2, 2)), 844),
 (((1, 2), 'BA', (0, 2)), 829),
 (((0, 2), 'AB', (1, 2)), 829),
 (((1, 1), 'RL', (1, 0)), 821),
 (((1, 0), 'LR', (1, 1)), 821),
 (((0, 1), 'RL', (0, 0)), 817),
 (((0, 0), 'LR', (0, 1)), 817),
 (((2, 0), 'LR', (2, 1)), 811),
 (((2, 1), 'RL', (2, 0)), 811),
 (((0, 2), 'RL', (0, 1)), 808),
 (((0, 1), 'LR', (0, 2)), 808),
 (((0, 0), 'AB', (1, 0)), 803),
 (((1, 0), 'BA', (0, 0)), 803),
 (((1, 1), 'BA', (0, 1)), 797),
 (((0, 1), 'AB', (1, 1)), 797),
 (((1, 2), 'RL', (1, 1), 'AB', (2, 1)), 266),
 (((2, 1), 'BA', (1, 1), 'LR', (1, 2)), 266),
 (((1, 2), 'RL', (1, 1), 'BA', (0, 1)), 257),
 (((0, 1), 'AB', (1, 1), 'LR', (1, 2)), 257),
 (((1, 2), 'AB', (2, 2), 'RL', (2, 1)), 252),
 (

In [41]:
Counter(all_positive_objattr_paths).most_common()

[(('red,rubber,cube', 'AB', 'green,metal,sphere'), 28),
 (('green,metal,sphere', 'BA', 'red,rubber,cube'), 28),
 (('green,metal,sphere', 'AB', 'green,rubber,cube'), 28),
 (('green,rubber,cube', 'BA', 'green,metal,sphere'), 28),
 (('green,rubber,tetrahedron', 'LR', 'blue,metal,sphere'), 27),
 (('blue,metal,sphere', 'RL', 'green,rubber,tetrahedron'), 27),
 (('blue,rubber,sphere', 'LR', 'green,rubber,sphere'), 27),
 (('green,rubber,sphere', 'RL', 'blue,rubber,sphere'), 27),
 (('red,metal,tetrahedron', 'BA', 'red,metal,sphere'), 25),
 (('red,metal,sphere', 'AB', 'red,metal,tetrahedron'), 25),
 (('green,rubber,cube', 'LR', 'blue,rubber,sphere'), 25),
 (('blue,rubber,sphere', 'RL', 'green,rubber,cube'), 25),
 (('green,rubber,sphere', 'AB', 'red,rubber,sphere'), 24),
 (('red,rubber,sphere', 'BA', 'green,rubber,sphere'), 24),
 (('blue,metal,sphere', 'LR', 'red,rubber,sphere'), 24),
 (('red,rubber,sphere', 'RL', 'blue,metal,sphere'), 24),
 (('blue,rubber,cube', 'BA', 'green,rubber,cube'), 24),


In [32]:
Counter(all_negative_objattr_paths).most_common()

[(('red,metal,tetrahedron', 'AB', 'blue,rubber,tetrahedron'), 31),
 (('red,rubber,sphere', 'AB', 'green,rubber,sphere'), 30),
 (('blue,rubber,sphere', 'RL', 'green,metal,tetrahedron'), 27),
 (('blue,rubber,sphere', 'LR', 'blue,rubber,tetrahedron'), 26),
 (('blue,metal,sphere', 'RL', 'blue,metal,cube'), 25),
 (('red,metal,sphere', 'RL', 'blue,rubber,cube'), 25),
 (('red,metal,cube', 'RL', 'red,rubber,sphere'), 25),
 (('blue,rubber,cube', 'RL', 'green,rubber,cube'), 25),
 (('red,rubber,tetrahedron', 'LR', 'blue,rubber,tetrahedron'), 25),
 (('green,metal,sphere', 'LR', 'red,rubber,cube'), 25),
 (('blue,metal,sphere', 'RL', 'red,rubber,sphere'), 25),
 (('red,metal,sphere', 'LR', 'red,metal,cube'), 25),
 (('blue,metal,tetrahedron', 'BA', 'blue,rubber,sphere'), 25),
 (('blue,rubber,cube', 'AB', 'red,metal,sphere'), 25),
 (('green,metal,sphere', 'AB', 'blue,metal,cube'), 24),
 (('red,rubber,tetrahedron', 'BA', 'green,metal,sphere'), 24),
 (('green,metal,sphere', 'AB', 'green,metal,cube'), 24)